In [1]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import warnings
warnings.filterwarnings('ignore')
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="0"
import pandas as pd
import numpy as np
from gtda.time_series import SlidingWindow
import matplotlib.pyplot as plt
from tensorflow.python.keras.backend import set_session
import tensorflow as tf
config = tf.compat.v1.ConfigProto() 
config.gpu_options.allow_growth = True  
config.log_device_placement = True  
sess2 = tf.compat.v1.Session(config=config)
set_session(sess2)  
from tensorflow.keras.layers import Dense, MaxPooling1D, Flatten
from tensorflow.keras import Input, Model
from tensorflow.keras.callbacks import ModelCheckpoint
import tensorflow.compat.v1.keras.backend as K
from tensorflow.keras.models import load_model
from tcn import TCN, tcn_full_summary
from tcn import compiled_tcn
from tensorflow.keras.utils import to_categorical
import csv
import random
import itertools
from keras_flops import get_flops
from mango.tuner import Tuner
import time
from tensorflow.keras.losses import MSE
import pickle
from hardware_utils import *
from data_utils import *

Device mapping:
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: NVIDIA GeForce RTX 3090, pci bus id: 0000:01:00.0, compute capability: 8.6



In [2]:
sampling_rate = 100
window_size = 550
stride = 50
epsilon = 0.4
f = '/home/nesl/earable/Earable/Activity_Dataset/' #dataset directory

X_tr, Y_tr, X_test, Y_test = import_auritus_activity_dataset(dataset_folder = f, 
                                use_timestamp=False, 
                                shuffle=True, 
                                window_size = window_size, stride = stride, 
                                return_test_set = True, test_set_size = 300,channels=0)


random_indices = np.random.choice(X_tr.shape[0], size=1000, replace=False)
X_val = X_tr[random_indices,:,:]
Y_val = Y_tr[random_indices,:]
X_tr = np.delete(X_tr,random_indices,axis=0)
Y_tr = np.delete(Y_tr,random_indices,axis=0)

print(X_tr.shape)
print(Y_tr.shape)
print(X_val.shape)
print(Y_val.shape)
print(X_test.shape)
print(Y_test.shape)

100%|█████████████████████████████████████████| 399/399 [00:11<00:00, 33.29it/s]


(13671, 550, 6)
(13671, 9)
(1000, 550, 6)
(1000, 9)
(300, 550, 6)
(300, 9)


In [3]:
def fgsm_attack(model, image, label, eps):
    image = tf.cast(image, tf.float32)
    with tf.GradientTape() as tape:
        tape.watch(image)
        pred = model(image)
        loss = MSE(label, pred)
        gradient = tape.gradient(loss, image)
        signedGrad = tf.sign(gradient)
        adversary = (image + (signedGrad * eps)).numpy()
        return adversary
    
def perform_fgsm_attack(data,lab,eps,my_model):
    countadv = 0
    for i in tqdm(range(len(data))):
        act = data[i,:,:].reshape(1,data.shape[1],data.shape[2])
        label = lab[i,:]
        actPred = my_model.predict(act)
        actPred = actPred.argmax()
        adversary = fgsm_attack(my_model,act, label, eps=eps)
        pred = my_model.predict(adversary)
        adversaryPred = pred[0].argmax()
        if actPred == adversaryPred:
            countadv += 1
        
 
    adv_accu = countadv / len(data)
    return adv_accu

In [4]:
dirpath="/home/nesl/Mbed Programs/auritus_tcn/" #hardware program directory - this is where the TCN deployment code is stored
device = "NUCLEO_L476RG" #which hardware to use
model_name = 'Auritus_noadv'+device+'.hdf5'
HIL = False #use real hardware or proxy?
quantization = False #use quantization or not?
model_epochs = 500 #epochs to train each model for
NAS_epochs = 50 #epochs for hyperparameter tuning
output_name = 'g_model_2.tflite'
log_file_name = 'TCN_Auritus_noadv_'+device+'.csv'
if os.path.exists(log_file_name):
    os.remove(log_file_name)
row_write = ['score', '1-accuracy','adv_accuracy','RAM','Flash','FLOPS','Latency','nb_filters','kernel_size',
             'dilations','use_skip_connections']
with open(log_file_name, 'a', newline='') as csvfile:
    csvwriter = csv.writer(csvfile)
    csvwriter.writerow(row_write)
if os.path.exists(log_file_name[0:-4]+'.p'):
    os.remove(log_file_name[0:-4]+'.p')

In [5]:
def objective_NN(epochs=1000,nb_filters=10,kernel_size=3,
                 dilations=[1, 2, 4, 8, 16, 32, 64, 128, 256],
                 use_skip_connections=True):
    
    err = 'inf'
    adv_accu = 'inf'
    input_dim=X_tr.shape[2]
    
    model = compiled_tcn(return_sequences=False,
                         num_feat=input_dim,
                         num_classes=Y_tr.shape[1],
                         nb_filters=nb_filters,
                         kernel_size=kernel_size,
                         dilations=dilations,
                         nb_stacks=1,
                         max_len=window_size,
                         use_weight_norm=False,
                         use_skip_connections=use_skip_connections)
    
    opt = tf.keras.optimizers.Adam()
    model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
                  optimizer=opt,metrics=['accuracy'])
    Flops = get_flops(model, batch_size=1)
    convert_to_tflite_model(model=model,training_data=X_tr,quantization=quantization,output_name=output_name) 
    maxRAM, maxFlash = return_hardware_specs(device)
    
    if(HIL==True):
        convert_to_cpp_model(dirpath)
        RAM, Flash, Latency, idealArenaSize, errorCode = HIL_controller(dirpath=dirpath,
                                                                       chosen_device=device,
                                                                       window_size=window_size, 
                                                                    number_of_channels = input_dim,
                                                                   quantization=quantization)     
        score = -5.0
        if(Flash==-1):
            row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
            print('Design choice:',row_write)
            with open(log_file_name, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                csvwriter.writerow(row_write)
            return score    
    
        elif(Flash!=-1):
            checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
            model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
                      epochs=epochs,callbacks=[checkpoint],shuffle=True,verbose=1)
            err = 1-checkpoint.best
            #adv_accu = perform_fgsm_attack(data=X_val, lab=Y_val,eps=epsilon,my_model=model)
            
            resource_usage = (RAM/maxRAM) + (Flash/maxFlash) 
            score = -err + 0.01*resource_usage - 0.05*Latency #- (0.5*(1-adv_accu)) #weigh each component as you like
                
            row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
            print('Design choice:',row_write)
            with open(log_file_name, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                csvwriter.writerow(row_write)   
    else:
        score = -5.0
        Flash = os.path.getsize(output_name)
        RAM = get_model_memory_usage(batch_size=1,model=model)
        Latency=-1
        max_flops = (30e6)
        
        if(RAM < maxRAM and Flash<maxFlash):
            checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
            model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
                      epochs=epochs,callbacks=[checkpoint],shuffle=True,verbose=1)
            err = 1-checkpoint.best 
            #adv_accu = perform_fgsm_attack(data=X_val, lab=Y_val,eps=epsilon,my_model=model)
            resource_usage = (RAM/maxRAM) + (Flash/maxFlash)
            score = -err + 0.01*resource_usage - 0.05*(Flops/max_flops)#- (0.5*(1-adv_accu))  #weigh each component as you like
        
        row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
        print('Design choice:',row_write)
        with open(log_file_name, 'a', newline='') as csvfile:
            csvwriter = csv.writer(csvfile)
            csvwriter.writerow(row_write) 
    
    return score        

In [6]:
import pickle 

def save_res(data, file_name):
    pickle.dump( data, open( file_name, "wb" ) )
    
min_layer = 3
max_layer = 8
a_list = [1,2,4,8,16,32,64,128,256]
all_combinations = []
dil_list = []
for r in range(len(a_list) + 1):
    combinations_object = itertools.combinations(a_list, r)
    combinations_list = list(combinations_object)
    all_combinations += combinations_list
all_combinations = all_combinations[1:]
for item in all_combinations:
    if(len(item) >= min_layer and len(item) <= max_layer):
        dil_list.append(list(item))

param_dict = {
    'nb_filters': range(2,64),
    'kernel_size': range(2,16),
    'use_skip_connections': [True, False],
    'dil_list': dil_list
}

def objfunc(args_list):

    objective_evaluated = []
    
    start_time = time.time()
    
    for hyper_par in args_list:
        nb_filters = hyper_par['nb_filters']
        kernel_size = hyper_par['kernel_size']
        use_skip_connections = hyper_par['use_skip_connections']
        dil_list = hyper_par['dil_list']
            
        objective = objective_NN(epochs=model_epochs,nb_filters=nb_filters,kernel_size=kernel_size,
                                 dilations=dil_list,use_skip_connections=use_skip_connections,)
        objective_evaluated.append(objective)
        
        end_time = time.time()
        print('objective:', objective, ' time:',end_time-start_time)
        
    return objective_evaluated

conf_Dict = dict()
conf_Dict['batch_size'] = 1 
conf_Dict['num_iteration'] = NAS_epochs
conf_Dict['initial_random']= 5
tuner = Tuner(param_dict, objfunc,conf_Dict)
all_runs = []
results = tuner.maximize()
all_runs.append(results)
save_res(all_runs,log_file_name[0:-4]+'.p')

x.shape= (None, 29)
model.x = (None, 550, 6)
model.y = (None, 9)
Instructions for updating:
Use `tf.compat.v1.graph_util.tensor_shape_from_node_def_name`

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              1
-min_occurrence             0
-step                       -1
-order_by                   float_ops
-account_type_regexes       .*
-start_name_regexes         .*
-trim_name_regexes          
-show_name_regexes          .*
-hide_name_regexes          
-account_displayed_op_only  true
-select                     float_ops
-output                     stdout:

==================Model Analysis Report======================

Doc:
scope: The nodes in the model graph are organized by 

INFO:tensorflow:Assets written to: /tmp/tmplcj1j6vx/assets


INFO:tensorflow:Assets written to: /tmp/tmplcj1j6vx/assets


Design choice: [-5.0, 'inf', 'inf', 481020.0, 487256, 133502366, -1, 29, 15, [2, 4, 8, 16, 128], True]
objective: -5.0  time: 3.7363929748535156
x.shape= (None, 2)
model.x = (None, 550, 6)
model.y = (None, 9)

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              1
-min_occurrence             0
-step                       -1
-order_by                   float_ops
-account_type_regexes       .*
-start_name_regexes         .*
-trim_name_regexes          
-show_name_regexes          .*
-hide_name_regexes          
-account_displayed_op_only  true
-select                     float_ops
-output                     stdout:

==================Model Analysis Report======================

Doc

INFO:tensorflow:Assets written to: /tmp/tmp9j60hos5/assets


...

428/428 [==============================] - 4s 8ms/step - loss: 0.2496 - accuracy: 0.9010 - val_loss: 0.2446 - val_accuracy: 0.9110

Epoch 00437: val_accuracy did not improve from 0.92500
Epoch 438/500
428/428 [==============================] - 4s 9ms/step - loss: 0.2497 - accuracy: 0.9004 - val_loss: 0.2358 - val_accuracy: 0.9060

Epoch 00438: val_accuracy did not improve from 0.92500
Epoch 439/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2471 - accuracy: 0.9017 - val_loss: 0.2554 - val_accuracy: 0.9070

Epoch 00439: val_accuracy did not improve from 0.92500
Epoch 440/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2480 - accuracy: 0.9025 - val_loss: 0.2393 - val_accuracy: 0.9020

Epoch 00440: val_accuracy did not improve from 0.92500
Epoch 441/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2424 - accuracy: 0.9037 - val_loss: 0.2373 - val_accuracy: 0.9080

Epoch 00441: val_accuracy did not improve from 0.92500
Epoch 442

428/428 [==============================] - 4s 8ms/step - loss: 0.2354 - accuracy: 0.9094 - val_loss: 0.2336 - val_accuracy: 0.9030

Epoch 00478: val_accuracy did not improve from 0.92500
Epoch 479/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2375 - accuracy: 0.9059 - val_loss: 0.2282 - val_accuracy: 0.9170

Epoch 00479: val_accuracy did not improve from 0.92500
Epoch 480/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2528 - accuracy: 0.8993 - val_loss: 0.2341 - val_accuracy: 0.9060

Epoch 00480: val_accuracy did not improve from 0.92500
Epoch 481/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2324 - accuracy: 0.9063 - val_loss: 0.2272 - val_accuracy: 0.9040

Epoch 00481: val_accuracy did not improve from 0.92500
Epoch 482/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2373 - accuracy: 0.9071 - val_loss: 0.2098 - val_accuracy: 0.9160

Epoch 00482: val_accuracy did not improve from 0.92500
Epoch 483

INFO:tensorflow:Assets written to: /tmp/tmp1mm76xxs/assets


INFO:tensorflow:Assets written to: /tmp/tmp1mm76xxs/assets


Design choice: [-5.0, 'inf', 'inf', 421644.0, 427200, 123638160, -1, 47, 5, [2, 8, 32, 64, 256], False]
objective: -5.0  time: 3.0278549194335938


# Train the best model

In [7]:
input_dim=X_tr.shape[2]

model = compiled_tcn(return_sequences=False,
                     num_feat=input_dim,
                     num_classes=Y_tr.shape[1],
                     nb_filters=results['best_params']['nb_filters'],
                     kernel_size=results['best_params']['kernel_size'],
                     dilations=results['best_params']['dil_list'],
                     nb_stacks=1,
                     max_len=window_size,
                     use_weight_norm=False,
                     use_skip_connections=results['best_params']['use_skip_connections'])

opt = tf.keras.optimizers.Adam()
model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
              optimizer=opt,metrics=['accuracy'])

checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
          epochs=model_epochs,callbacks=[checkpoint],shuffle=True,verbose=1)

model = load_model(model_name,custom_objects={'TCN': TCN})
test_accu = model.evaluate(x=X_test,y=Y_test)[1]
print('Test Accuracy:', test_accu)
adv_accu = perform_fgsm_attack(data=X_test, lab=Y_test,eps=epsilon,my_model=model)
print('Adversarial Accuracy:', adv_accu)

x.shape= (None, 8)
model.x = (None, 550, 6)
model.y = (None, 9)
Epoch 1/500
428/428 [==============================] - 5s 9ms/step - loss: 29.5802 - accuracy: 0.1252 - val_loss: 8.6876 - val_accuracy: 0.1480

Epoch 00001: val_accuracy improved from -inf to 0.14800, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 2/500
428/428 [==============================] - 4s 8ms/step - loss: 6.6824 - accuracy: 0.1616 - val_loss: 3.7688 - val_accuracy: 0.2350

Epoch 00002: val_accuracy improved from 0.14800 to 0.23500, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 3/500
428/428 [==============================] - 4s 8ms/step - loss: 3.4647 - accuracy: 0.2452 - val_loss: 2.4939 - val_accuracy: 0.2800

Epoch 00003: val_accuracy improved from 0.23500 to 0.28000, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 4/500
428/428 [==============================] - 4s 8ms/step - loss: 2.4112 - accuracy: 0.2801 - val_loss: 1.9108 - val_accuracy: 0.3300

Epoch 00004: val_accuracy improved fro

428/428 [==============================] - 4s 9ms/step - loss: 0.9047 - accuracy: 0.6397 - val_loss: 0.8456 - val_accuracy: 0.6420

Epoch 00035: val_accuracy did not improve from 0.65400
Epoch 36/500
428/428 [==============================] - 4s 8ms/step - loss: 0.8957 - accuracy: 0.6455 - val_loss: 0.8088 - val_accuracy: 0.6830

Epoch 00036: val_accuracy improved from 0.65400 to 0.68300, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 37/500
428/428 [==============================] - 3s 8ms/step - loss: 0.8836 - accuracy: 0.6505 - val_loss: 0.8109 - val_accuracy: 0.6660

Epoch 00037: val_accuracy did not improve from 0.68300
Epoch 38/500
428/428 [==============================] - 4s 8ms/step - loss: 0.8680 - accuracy: 0.6559 - val_loss: 0.7840 - val_accuracy: 0.6830

Epoch 00038: val_accuracy did not improve from 0.68300
Epoch 39/500
428/428 [==============================] - 4s 8ms/step - loss: 0.8628 - accuracy: 0.6602 - val_loss: 0.7919 - val_accuracy: 0.6890

Epoch 00039: va


Epoch 00071: val_accuracy did not improve from 0.82200
Epoch 72/500
428/428 [==============================] - 4s 8ms/step - loss: 0.5415 - accuracy: 0.7809 - val_loss: 0.4754 - val_accuracy: 0.8320

Epoch 00072: val_accuracy improved from 0.82200 to 0.83200, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 73/500
428/428 [==============================] - 3s 8ms/step - loss: 0.5347 - accuracy: 0.7822 - val_loss: 0.4648 - val_accuracy: 0.8070

Epoch 00073: val_accuracy did not improve from 0.83200
Epoch 74/500
428/428 [==============================] - 3s 8ms/step - loss: 0.5302 - accuracy: 0.7833 - val_loss: 0.4656 - val_accuracy: 0.8230

Epoch 00074: val_accuracy did not improve from 0.83200
Epoch 75/500
428/428 [==============================] - 4s 8ms/step - loss: 0.5316 - accuracy: 0.7831 - val_loss: 0.4861 - val_accuracy: 0.7980

Epoch 00075: val_accuracy did not improve from 0.83200
Epoch 76/500
428/428 [==============================] - 4s 8ms/step - loss: 0.5211 - accura


Epoch 00111: val_accuracy did not improve from 0.84600
Epoch 112/500
428/428 [==============================] - 4s 8ms/step - loss: 0.4189 - accuracy: 0.8277 - val_loss: 0.4129 - val_accuracy: 0.8380

Epoch 00112: val_accuracy did not improve from 0.84600
Epoch 113/500
428/428 [==============================] - 4s 8ms/step - loss: 0.4147 - accuracy: 0.8329 - val_loss: 0.3871 - val_accuracy: 0.8400

Epoch 00113: val_accuracy did not improve from 0.84600
Epoch 114/500
428/428 [==============================] - 4s 9ms/step - loss: 0.4091 - accuracy: 0.8319 - val_loss: 0.3982 - val_accuracy: 0.8450

Epoch 00114: val_accuracy did not improve from 0.84600
Epoch 115/500
428/428 [==============================] - 3s 8ms/step - loss: 0.4107 - accuracy: 0.8305 - val_loss: 0.4040 - val_accuracy: 0.8510

Epoch 00115: val_accuracy improved from 0.84600 to 0.85100, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 116/500
428/428 [==============================] - 4s 8ms/step - loss: 0.4173 - a

428/428 [==============================] - 4s 8ms/step - loss: 0.3500 - accuracy: 0.8528 - val_loss: 0.3528 - val_accuracy: 0.8530

Epoch 00151: val_accuracy did not improve from 0.86200
Epoch 152/500
428/428 [==============================] - 4s 9ms/step - loss: 0.3537 - accuracy: 0.8540 - val_loss: 0.3649 - val_accuracy: 0.8590

Epoch 00152: val_accuracy did not improve from 0.86200
Epoch 153/500
428/428 [==============================] - 4s 8ms/step - loss: 0.3537 - accuracy: 0.8509 - val_loss: 0.3247 - val_accuracy: 0.8650

Epoch 00153: val_accuracy improved from 0.86200 to 0.86500, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 154/500
428/428 [==============================] - 4s 8ms/step - loss: 0.3539 - accuracy: 0.8518 - val_loss: 0.3427 - val_accuracy: 0.8540

Epoch 00154: val_accuracy did not improve from 0.86500
Epoch 155/500
428/428 [==============================] - 4s 8ms/step - loss: 0.3490 - accuracy: 0.8541 - val_loss: 0.3460 - val_accuracy: 0.8660

Epoch 00155

...

428/428 [==============================] - 3s 8ms/step - loss: 0.2640 - accuracy: 0.8903 - val_loss: 0.2733 - val_accuracy: 0.8920

Epoch 00392: val_accuracy did not improve from 0.90000
Epoch 393/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2750 - accuracy: 0.8890 - val_loss: 0.2594 - val_accuracy: 0.8970

Epoch 00393: val_accuracy did not improve from 0.90000
Epoch 394/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2734 - accuracy: 0.8891 - val_loss: 0.2832 - val_accuracy: 0.8900

Epoch 00394: val_accuracy did not improve from 0.90000
Epoch 395/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2670 - accuracy: 0.8934 - val_loss: 0.2651 - val_accuracy: 0.9030

Epoch 00395: val_accuracy improved from 0.90000 to 0.90300, saving model to Auritus_noadvNUCLEO_L476RG.hdf5
Epoch 396/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2746 - accuracy: 0.8890 - val_loss: 0.2641 - val_accuracy: 0.9040

Epoch 00396

428/428 [==============================] - 3s 8ms/step - loss: 0.2698 - accuracy: 0.8917 - val_loss: 0.2669 - val_accuracy: 0.8920

Epoch 00432: val_accuracy did not improve from 0.90400
Epoch 433/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2647 - accuracy: 0.8925 - val_loss: 0.2823 - val_accuracy: 0.8890

Epoch 00433: val_accuracy did not improve from 0.90400
Epoch 434/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2612 - accuracy: 0.8949 - val_loss: 0.2616 - val_accuracy: 0.8940

Epoch 00434: val_accuracy did not improve from 0.90400
Epoch 435/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2734 - accuracy: 0.8909 - val_loss: 0.2743 - val_accuracy: 0.8930

Epoch 00435: val_accuracy did not improve from 0.90400
Epoch 436/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2644 - accuracy: 0.8904 - val_loss: 0.2824 - val_accuracy: 0.8950

Epoch 00436: val_accuracy did not improve from 0.90400
Epoch 437


Epoch 00472: val_accuracy did not improve from 0.90500
Epoch 473/500
428/428 [==============================] - 4s 8ms/step - loss: 0.2644 - accuracy: 0.8949 - val_loss: 0.2579 - val_accuracy: 0.8920

Epoch 00473: val_accuracy did not improve from 0.90500
Epoch 474/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2568 - accuracy: 0.8953 - val_loss: 0.2575 - val_accuracy: 0.8960

Epoch 00474: val_accuracy did not improve from 0.90500
Epoch 475/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2526 - accuracy: 0.8996 - val_loss: 0.2539 - val_accuracy: 0.8900

Epoch 00475: val_accuracy did not improve from 0.90500
Epoch 476/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2555 - accuracy: 0.8975 - val_loss: 0.2663 - val_accuracy: 0.8950

Epoch 00476: val_accuracy did not improve from 0.90500
Epoch 477/500
428/428 [==============================] - 3s 8ms/step - loss: 0.2694 - accuracy: 0.8918 - val_loss: 0.2525 - val_accuracy: 0.

100%|█████████████████████████████████████████| 300/300 [00:21<00:00, 13.85it/s]

Adversarial Accuracy: 0.14333333333333334
